In [1]:
import argparse
import importlib
import json
import logging
import os
import time
import sys
import numpy as np

from matplotlib import pyplot as plt
from tensorforce import TensorForceError
from tensorforce.agents import DQNAgent
from tensorforce.execution import Runner
from surface_env import *
import ase.io


/home/zulissi/miniconda3/envs/tensorforce/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/zulissi/miniconda3/envs/tensorforce/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/zulissi/miniconda3/envs/tensorforce/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/home/zulissi/miniconda3/

In [2]:
def plot_energy(energy, ylabel, save_path):
    plt.figure()
    plt.xlabel('training episode')
    plt.ylabel(ylabel)
    plt.title('episode vs. ' + ylabel)
    plt.plot(energy)
    plt.savefig(save_path)
    print('figure saved as {}'.format(save_path))
    return 

In [3]:
episodes=100000
horizon=200
deterministic=False

In [ ]:

env = SurfaceEnv(horizon)
print('Initial energy:', env.get_energy())

# lattice = Surface()
# lattice.reset()
# print(lattice.current_positions())
# print(lattice.current_positions().shape)
# print(type(lattice.current_positions()))

network_spec = [
    {
        "type": "dense",
        "size": 64,
        "activation": "relu"
    },
    {
        "type": "dense",
        "size": 32,
        "activation": "relu"
    }
    # {
    #     "type": "dense",
    #     "size": 6+32,
    #     "activation": "softmax"
    # }
]

# print(env.states)
# print(env.states['shape'])

agent = DQNAgent(
    states=env.states,
    actions=env.actions,
    network=network_spec,
    batched_observe=True, 
    batching_capacity=8000,
    execution=dict(
        type='single',
        session_config=None,
        distributed_spec=None
    ), 

    states_preprocessing=None,
    reward_preprocessing=None,

    update_mode=dict(
        unit='timesteps',
        batch_size=10,
        frequency=10
    ),
    memory=dict(
        type='replay',
        include_next_states=True,
        capacity=40000
    ),

    optimizer=dict(
        type='clipped_step',
        clipping_value=0.1,
        optimizer=dict(
            type='adam',
            learning_rate=1e-3
        )
    ),
    actions_exploration=dict(
        type='epsilon_anneal',
        initial_epsilon=0.5,
        final_epsilon=0.05,
        timesteps=1000000
    ),
    discount=1,
    distributions=None,
    entropy_regularization=0.01,
    target_sync_frequency=1000,
    target_update_weight=1.0,
    double_q_model=False,
    huber_loss=None,

    summarizer=dict(
        directory=None,
        labels=['graph', 'total-loss']
    ),
)

runner = Runner(
    agent=agent,
    environment=env,
    repeat_actions=1
)

cur_min = -1e6

energies_list = [env.initial_energy]

def episode_finished(r):
    
    global cur_min
    # positions = env.get_positions()
    # print("pos diff:", np.sum(positions[1,:] - positions[0,:]))
    # np.save('shit', positions)
    
    energy_dist = np.min(np.abs(np.array(energies_list)-env.get_energy()))
    print(env.get_energy())
    print(energy_dist)
    print(energies_list)
    if r.episode % 100 == 0 \
            or r.episode_rewards[-1]>cur_min \
            or energy_dist>0.05:
        final_energy = env.get_energy()
        positions = env.get_positions()
        
        image_list = []
        with ase.io.trajectory.TrajectoryWriter('gifs/%d_%1.2f_%1.2f.traj'%(r.episode,final_energy, r.episode_rewards[-1])) as traj:
            for pos in positions:
                env._lattice.set_free_atoms(pos)
                copy_atoms = env._lattice.atoms.copy()
                image_list.append(copy_atoms.repeat((2,2,1)))
                traj.write(copy_atoms, energy=env.get_energy())

#         ase.io.write('gifs/%d_%1.2f.gif'%(r.episode,final_energy) , image_list, interval=100)
        
        if final_energy > cur_min:
            cur_min = r.episode_rewards[-1]
            
        if energy_dist>0.05:
            energies_list.append(env.get_energy())
    if r.episode % 50 == 0:
        positions = env.get_positions()
        pos_fn = '_'.join(['pos_3', str(r.episode)])
        pos_dir = os.path.join('new_pos', pos_fn)
        np.save(pos_dir, positions)
    if r.episode % 50 == 0:
        agent_fn = '_'.join(['agent_3', str(r.episode)])
        agent_dir = os.path.join('new_agents', agent_fn)
        r.agent.save_model(agent_dir)
        print("Saving agent to {}".format(agent_dir))
    if r.episode % 50 == 0:
        rew_fn = '.'.join(['_'.join(['reward_3', str(r.episode)]), 'png'])
        rew_dir = os.path.join('new_plots', rew_fn)
        plot_energy(r.episode_rewards, 'accumulated reward', rew_dir)
        energy_fn = '.'.join(['_'.join(['final', 'energy_3', str(r.episode)]), 'png'])
        energy_dir = os.path.join('new_plots', energy_fn)
        plot_energy(env.final_energy, 'final energy', energy_dir)
    print("Finished episode {ep} after {ts} timesteps (reward: {reward})".
        format(ep=r.episode, ts=r.episode_timestep,reward=r.episode_rewards[-1]))
    return True

runner.run(
    # num_timesteps=args.timesteps,
    num_episodes=episodes,
    max_episode_timesteps=horizon,
    deterministic=deterministic,
    episode_finished=episode_finished
)
runner.close()

Initial energy: 2.1797225799832667


  0%|          | 0/100000 [00:00<?, ?it/s]

0.005059399470666963
0.18329826355447418
0.25769914494652923
0.3632769713255568
0.4068695292038362
0.5754164773308537
0.7724412152216805
0.7979131725777857
1.0011127506741913
1.0207128975447795
1.021783720375464
1.2286591389859203
1.4405431574246292
1.6555137864095906
1.6485974976360502
1.6604796664653085
1.8769001122420026
1.8769001122420026
1.8901730162432333
2.106730960498597
2.097304760942369
2.316084749930543
2.53570697783678
2.5932317831695975
2.812142851412288
2.8210188614664076
3.283563627791398
3.0639154798770023
2.844884187081302
2.626624070547697
2.4093447196397335
2.1933376274826415
2.4093447196397357
2.4177083981332523
2.448533009457716
2.2363143492092896
2.026546283348763
1.8200763194520158
1.8579550108016316
1.6606579395643786
1.4709088218898954
1.2920374345926797
1.1292248237017046
1.1283843780048102
1.1459717730054706
1.0094747518391014
0.9082000025742832
0.8547603259108613
0.8581393737771013
0.9177097334679791
0.9809134288518371
1.0309748409147106
0.9545279391904316
0

/home/zulissi/software/sella/sella/sella.py:28: UserWarning: ASE Atoms object has attached constraints, but these will be ignored! Please provide constraints to the MinMode object initializer instead!
  warnings.warn('ASE Atoms object has attached constraints, '


[0.15175572 0.10158615 3.202845   9.09003405] [-1.51671109e+03 -1.49986065e+03 -1.14710994e+00  2.04106718e+01] [-1.00055787e-04 -6.77303926e-05 -2.79209941e+00  4.45356926e-01] 2
[2.04261339e-03 1.51867203e-02 2.55145981e+00 1.12254282e+01] [-1516.71111367 -1499.86065423    -1.60856926    11.99954027] [-1.34673859e-06 -1.01254208e-05 -1.58616721e+00  9.35488187e-01] 2
[1.23716083e-03 1.51800058e-02 2.32079805e+00 7.93874868e+00] [-1516.71111366 -1499.86065423    -1.97900864     5.37352102] [-8.15686533e-07 -1.01209441e-05 -1.17270739e+00  1.47738301e+00] 2
[1.21459633e-03 1.49419877e-02 2.22141938e+00 4.47932315e+00] [-1.51671111e+03 -1.49986065e+03 -2.49220086e+00  1.33537098e+00] [-8.00809278e-07 -9.96225058e-06 -8.91348452e-01  3.35436610e+00] 2
[1.16463075e-03 1.43275522e-02 1.17575596e+00 1.92515865e+00] [-1.51671111e+03 -1.49986065e+03 -2.81285561e+00  2.45839577e-01] [-7.67865903e-07 -9.55258887e-06 -4.17993713e-01  7.83095496e+00] 2
[1.05938880e-03 1.30329173e-02 2.01742877e+0

...

  0%|          | 470/100000 [1:14:13<184:50:13,  6.69s/it]

Episode ends and final energy: 2.217433374840084
2.2174333748400823
0.03771079485681561
[2.1797225799832667, 3.2085608975422915, 3.628438374212317, 7.078174244008197, 3.8211275900855695, 32.81621985534106, 30.178867968375243, 3.4392093519395317, 7.286415028445704, 6.106237978583589, 7.230743967601061, 5.656070759908257, 5.4426431199014065, 3.955183421567641, 30.311662136490632, 3.2763168102966773, 7.478224125987604, 4.106043100105188, 3.3428115996599708, 3.884104586110709, 4.491755359331805, 6.598860092604104, 4.364936475337261, 26.318440160887405, 3.496409676947186, 29.61269723598506, 30.24884957312473, 6.882305881807396, 2.3924090974241743, 66.4934436242852, 6.996553299212669, 29.768708687106866, 3.5480762453909467, 29.685459067770896, 6.703055438477007, 4.038227642268398, 30.490536729853005, 2.1270464255725336, 2.256647520197271, 26.817048104923696, 29.975740354006657, 5.961197863992515, 2.309445005834622, 2.476886838063681, 6.500241160284815, 13.494318775028297, 13.36793406118568, 

[1.38098018 4.02108836] [0.77078703 5.80708194] [1.79164947 0.6924456 ] 0
[1.12231231 2.5065007 ] [0.45209153 3.28548438] [2.48248914 0.76290142] 0
[1.10338968 2.15967729] [0.24534974 2.31010517] [4.49721149 0.93488267] 0
[0.80078868 1.4578139 ] [0.11616027 1.83448923] [6.89382609 0.79467018] 0
[0.54539191 1.04728636] [0.05352496 1.61225197] [10.18948813  0.64957983] 0
[0.46780577 1.08774542] [0.00624028 1.39393287] [74.96555342  0.78034276] 0
[0.61090724 1.64807305] [-0.05125999  0.98359046] [-11.91781782   1.67556834] 0
[0.5955946 1.1319903] [-0.12740089  0.56111234] [-4.67496411  2.01740404] 0
[0.69389894 0.71514522] [-0.28513227  0.23718316] [-2.43360371  3.01516017] 0
[1.00229554 0.6451413 ] [-0.54065498  0.06732507] [-1.85385427  9.58248203] 0
[0.77516677 0.41829289 0.82713213] [-0.83442792 -0.03336197  0.69061849] [ -0.92897989 -12.53801662   1.19766868] 0
[0.38608182 0.24103312 0.46213002] [-0.96534725 -0.07720459  0.52058988] [-0.39994087 -3.12200496  0.88770457] 0
[0.26018245

  0%|          | 471/100000 [1:14:20<188:55:31,  6.83s/it]

Episode ends and final energy: 2.184006755031934
2.184006755031911
0.004284175048644201
[2.1797225799832667, 3.2085608975422915, 3.628438374212317, 7.078174244008197, 3.8211275900855695, 32.81621985534106, 30.178867968375243, 3.4392093519395317, 7.286415028445704, 6.106237978583589, 7.230743967601061, 5.656070759908257, 5.4426431199014065, 3.955183421567641, 30.311662136490632, 3.2763168102966773, 7.478224125987604, 4.106043100105188, 3.3428115996599708, 3.884104586110709, 4.491755359331805, 6.598860092604104, 4.364936475337261, 26.318440160887405, 3.496409676947186, 29.61269723598506, 30.24884957312473, 6.882305881807396, 2.3924090974241743, 66.4934436242852, 6.996553299212669, 29.768708687106866, 3.5480762453909467, 29.685459067770896, 6.703055438477007, 4.038227642268398, 30.490536729853005, 2.1270464255725336, 2.256647520197271, 26.817048104923696, 29.975740354006657, 5.961197863992515, 2.309445005834622, 2.476886838063681, 6.500241160284815, 13.494318775028297, 13.36793406118568, 